In [0]:
#!pip install numpy==1.16.2



In [0]:
# neccesary library
import os
import numpy as np
import tensorflow as tf
from tensorflow.keras.layers import Input, Dense, Flatten,Conv2D, MaxPooling2D, Concatenate,InputLayer
from tensorflow.keras.layers import Dropout
from tensorflow.keras.models import Sequential
from tensorflow.keras.models import Model

In [0]:
%load_ext tensorboard
import datetime
logdir = os.path.join("logs", datetime.datetime.now().strftime("%Y%m%d-%H%M%S"))
tensorboard_callback = tf.keras.callbacks.TensorBoard(logdir, histogram_freq=1)

In [0]:
# Define hyper parameters
ımage_size = 300

In [0]:
# Loading train data and test data
data = np.load('/content/drive/My Drive/Colab Notebooks/planet_classification_w_localization/dataset.npy')

In [0]:
# Separating train and validation sets
train = data[:int(len(data)*0.8)]
test = data[int(len(data)*0.8):]

In [0]:
# x_train for train input, images
x_train = np.array([i[0] for i in train]).reshape(-1,ımage_size,ımage_size,3)
# y_train1 for classification head, types
y_train1 = np.array([i[1] for i in train])
# y_train2 for regression head, localization
y_train2 = np.array([i[2] for i in train])

In [0]:
# x_test for test input, images
x_test = np.array([i[0] for i in test]).reshape(-1,ımage_size,ımage_size,3)
# y_test1 for classification head, types
y_test1 = np.array([i[1] for i in test])
# y_test2 for regression head, localization
y_test2 = np.array([i[2] for i in test])

In [0]:
# Define conv layers 
# First inputs and layers
inputs = Input(batch_shape=(None,300,300,3),name='i_images')
h = Conv2D(96,11,activation='relu',strides=4,padding='valid')(inputs)
h = MaxPooling2D(3,strides=2,padding='valid')(h) 
h = Conv2D(256,5,activation='relu',strides=1,padding='same')(h)
h = MaxPooling2D(3,strides=2,padding='valid')(h)
h = Conv2D(384,3,activation='relu',strides=1,padding='same')(h)
h = Conv2D(384,3,activation='relu',strides=1,padding='same')(h)
h = Conv2D(256,3,activation='relu',strides=1,padding='same')(h)
h = MaxPooling2D(3,strides=2,padding='valid')(h)
h = Flatten()(h)
# Second inputs and layers
h = Dense(4096,activation='relu')(h)
h = Dropout(0.50)(h)
h = Dense(4096,activation='relu')(h)
h = Dropout(0.50)(h)
class_outputs = Dense(4,activation='softmax',name='class_outputs')(h)
corr_outputs  = Dense(4,name='corr_outputs')(h)

model = Model(inputs=inputs, outputs=[class_outputs,corr_outputs])
model.compile(loss={'class_outputs':'categorical_crossentropy','corr_outputs':'mse'},
              loss_weights={'class_outputs':10,'corr_outputs':1},
              metrics={'class_outputs':'accuracy','corr_outputs':'mean_absolute_error'},
              optimizer = tf.keras.optimizers.Adam(0.00001))

history = model.fit({'i_images':x_train},
                    {'class_outputs':y_train1,'corr_outputs':y_train2},
                    validation_split = 0.2, epochs =1000,
                    callbacks=[tensorboard_callback])


Epoch 1/1000
41/41 [==============================] - 8s 207ms/step - loss: 7514.9912 - class_outputs_loss: 17.5213 - corr_outputs_loss: 7339.7783 - class_outputs_accuracy: 0.2700 - corr_outputs_mean_absolute_error: 64.0211 - val_loss: 2743.8472 - val_class_outputs_loss: 1.7507 - val_corr_outputs_loss: 2726.3403 - val_class_outputs_accuracy: 0.3913 - val_corr_outputs_mean_absolute_error: 43.2242
Epoch 2/1000
41/41 [==============================] - 8s 191ms/step - loss: 3091.9268 - class_outputs_loss: 16.8885 - corr_outputs_loss: 2923.0408 - class_outputs_accuracy: 0.2802 - corr_outputs_mean_absolute_error: 44.0228 - val_loss: 2318.6809 - val_class_outputs_loss: 1.1858 - val_corr_outputs_loss: 2306.8230 - val_class_outputs_accuracy: 0.5807 - val_corr_outputs_mean_absolute_error: 40.6125
Epoch 3/1000
41/41 [==============================] - 8s 192ms/step - loss: 2738.8247 - class_outputs_loss: 14.5660 - corr_outputs_loss: 2593.1653 - class_outputs_accuracy: 0.3175 - corr_outputs_mean_ab

In [0]:
model.evaluate(x_test,[y_test1,y_test2])

In [0]:
model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
i_images (InputLayer)           [(None, 300, 300, 3) 0                                            
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 73, 73, 96)   34944       i_images[0][0]                   
__________________________________________________________________________________________________
max_pooling2d (MaxPooling2D)    (None, 36, 36, 96)   0           conv2d[0][0]                     
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 36, 36, 256)  614656      max_pooling2d[0][0]              
______________________________________________________________________________________________

In [0]:
%tensorboard --logdir logs

Output hidden; open in https://colab.research.google.com to view.

In [0]:
def model_save(model,path='/content/drive/My Drive/Colab Notebooks/planet_classification_w_localization/dnnmodel'):
  if not os.path.exists(path):
    os.mkdir(path)
  model.save(os.path.join(path,"model.h5"))
  print('Model save succesfully')
model_save(model)